<a href="https://colab.research.google.com/github/MachineSaver/animated-system/blob/main/Vibration_Primer.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
# !pip install plotly
# !pip install pandas
# !pip install scipy

# Working in 3D Space with Plotly Template

In [3]:
import plotly
import plotly.graph_objects as go
import plotly.io as pio
import plotly.express as px
import numpy as np
from scipy.fft import fft, fftfreq
import pandas as pd

def set_plotly_theme(name='Machine Saver Inc.'):
  pio.templates["draft"] = go.layout.Template(
    layout_annotations=[
        dict(
            name="draft watermark",
            text=name,
            textangle=-30,
            opacity=0.1,
            font=dict(color="white", size=50),
            xref="paper",
            yref="paper",
            x=0.5,
            y=0.5,
            showarrow=False,
          )
      ]
  )
  pio.templates.default = "plotly_dark+draft"

def shift_phase(degrees):
    deg_to_rad = np.pi / 180 # degrees to radians conversion
    return(degrees*deg_to_rad)

set_plotly_theme()

# Helix equation
t = np.linspace(0, 10, 50)
x, y, z = np.cos(t), np.sin(t), t

fig = px.scatter_3d(
    title="3D Helix/Spiral Plot"
    )
fig.add_scatter3d(
  x=x,
  y=y,
  z=z,
  mode="lines",
  name="scatter_1")
fig.add_scatter3d(
  x=-x,
  y=-y,
  z=np.linspace(0, 1, 50),
  mode="lines",
  name="scatter_1")
fig.show()


# Individual Sine Waves Added Together
## Result in a combined or convoluted waveform

In [4]:
start = 0
stop = 0.1
steps = 8192
t = np.linspace(start, stop, steps)

colors = [
'aliceblue', 'antiquewhite', 'aqua', 'aquamarine',
'azure', 'beige', 'bisque', 'blue', 'blueviolet',
'brown', 'cadetblue', 'chartreuse', 'coral',
'cornflowerblue', 'cornsilk', 'cyan', 'darkblue',
'darkcyan', 'darkgray', 'darkgreen', 'darkmagenta',
'darkolivegreen', 'darkorange', 'darkorchid', 'darkred',
'darksalmon', 'darkseagreen', 'darkslateblue',
'darkslategray', 'darkturquoise', 'darkviolet',
'deeppink', 'deepskyblue', 'dodgerblue', 'firebrick',
'floralwhite', 'forestgreen', 'fuchsia', 'gold',
'goldenrod', 'gray', 'green', 'greenyellow',
'honeydew', 'hotpink', 'indigo', 'ivory', 'khaki',
'lavender', 'lavenderblush', 'lightcoral',
'lightcyan', 'lightgray', 'lightgreen', 'lightpink',
'lightsalmon', 'lightseagreen', 'lightskyblue',
'lightslategray', 'lightsteelblue', 'lightyellow',
'lime', 'limegreen', 'linen', 'magenta',
'mediumaquamarine', 'mediumblue', 'mediumorchid',
'mediumpurple', 'mediumseagreen', 'mediumslateblue',
'mediumspringgreen', 'mediumturquoise',
'mediumvioletred', 'midnightblue', 'mintcream',
'mistyrose', 'moccasin', 'navajowhite', 'olive',
'olivedrab', 'orange', 'orangered', 'orchid',
'palegoldenrod', 'palegreen', 'paleturquoise',
'palevioletred', 'papayawhip', 'peachpuff', 'peru',
'pink', 'plum', 'powderblue', 'purple', 'rosybrown',
'saddlebrown', 'sandybrown', 'seagreen', 'seashell',
'sienna', 'skyblue', 'slateblue', 'slategray',
'snow', 'springgreen', 'steelblue', 'tan', 'thistle',
'tomato', 'turquoise', 'violet', 'wheat',
'whitesmoke', 'yellow', 'yellowgreen'
]

frequencies = [
    5,
    15,
    75,
    250,
    1000,
    2500,
    2650,
    3700,
    4075,
    6200
]

amplitudes = [
    0.25,
    2.1,
    1.025,
    0.75,
    2.4,
    1.1,
    3.4,
    0.95,
    1.85,
    1.62
]

combined = 0
for idx,frequency in enumerate(frequencies):
  combined += amplitudes[idx] * np.sin(2 * np.pi * frequency * t)

sinusoids = []
for idx,frequency in enumerate(frequencies):
  sinusoids.append(amplitudes[idx] * np.sin(2 * np.pi * frequency * t))

# Create the plot
fig = go.Figure()

for idx,sinusoid in enumerate(sinusoids):
  fig.add_trace(go.Scatter(x=t, y=sinusoid, mode='lines', name=str(frequencies[idx]), line=dict(color=colors[idx])))
  # pass
# fig.add_trace(go.Scatter(x=t, y=blue, mode='lines', name='Axis 1', line=dict(color='blue')))

fig.add_trace(go.Scatter(x=t, y=combined, mode='lines', name='combined', line=dict(color='#FFFFFF')))

fig.update_layout(title='Time Waveform Analysis Data', xaxis_title='Time (s)', yaxis_title='Acceleration (g)')

opacity = {'0.0': 0.25, '1.0': 0.65, '3.0': 0.05}
fig.for_each_trace(lambda trace: trace.update(opacity = opacity[trace.name]) if trace.name in opacity.keys() else (),)


fig.show()


# Convert from Acceleration Waveform to Velocity Waveform to Solve Certain Machine Problems

In [5]:
def acceleration_to_velocity(acceleration, time):
    # Convert acceleration from g to m/s^2
    acceleration_m_s2 = acceleration * 9.81

    # Calculate the time step
    dt = time[1] - time[0]

    # Integrate acceleration to get velocity
    velocity = np.cumsum(acceleration_m_s2) * dt

    return velocity

# Calculate velocity waveform
velocity = acceleration_to_velocity(combined, t)

# Create a new plot for the velocity waveform
fig_velocity = go.Figure()

fig_velocity.add_trace(go.Scatter(x=t, y=velocity, mode='lines', name='Velocity', line=dict(color='#FFFFFF')))

fig_velocity.update_layout(title='Velocity Waveform Analysis Data', xaxis_title='Time (s)', yaxis_title='Velocity (m/s)')

fig_velocity.show()


# Perform an FFT on the Velocity Time Waveform to Produce a Spectrum

In [6]:
# Sampling rate (samples per second)
fs = 8192

# Calculate the FFT
N = len(t)

# Generate the frequencies associated with the FFT
xf = fftfreq(N, 0.1 / fs)

# Create the plot
fig_fft = go.Figure()

# We only plot the positive frequencies (up to the Nyquist frequency)
mask = (xf >= 0) & (xf <= fs/2)


fig_fft.add_trace(go.Scatter(x=xf[mask], y=2.0/N * np.abs(fft(velocity))[mask], mode='lines', name=str(frequencies[idx]), line=dict(color=colors[idx])))

fig_fft.update_layout(title='Velocity Spectrum Analysis Data', xaxis_title='Frequency (Hz)', yaxis_title='Velocity')

fig_fft.show()


# Each Time Waveform Run Through a Fast Fourier Transform and Plotted

In [7]:
# Sampling rate (samples per second)
fs = 8192

# Calculate the FFT
N = len(t)
spectra = []
for each in sinusoids:
  spectra.append(fft(each))

# Generate the frequencies associated with the FFT
xf = fftfreq(N, 0.1 / fs)

# Create the plot
fig_fft = go.Figure()

# We only plot the positive frequencies (up to the Nyquist frequency)
mask = (xf >= 0) & (xf <= fs/2)

for idx,spectrum in enumerate(spectra):
  fig_fft.add_trace(go.Scatter(x=xf[mask], y=2.0/N * np.abs(spectrum)[mask], mode='lines', name=str(frequencies[idx]), line=dict(color=colors[idx])))

fig_fft.update_layout(title='Acceleration Spectrum Analysis Data', xaxis_title='Frequency (Hz)', yaxis_title='Acceleration')

fig_fft.show()


# Each Time Waveform Added Together, The Resulting Combined/Convoluted Waveform is run through a Fast Fourier Transform and Plotted

In [8]:
# Sampling rate (samples per second)
fs = 8192

# Calculate the FFT
N = len(t)
c_fft = fft(combined)
# Generate the frequencies associated with the FFT
xf = fftfreq(N, 0.1 / fs)

# Create the plot
fig_fft = go.Figure()

# We only plot the positive frequencies (up to the Nyquist frequency)
nyquist_freq = fs / 2
mask = (xf >= 0) & (xf <= nyquist_freq)

fig_fft.add_trace(go.Scatter(x=xf[mask], y=2.0/N * np.abs(c_fft[mask]), mode='lines', name='Combined', line=dict(color='#FFFFFF')))

fig_fft.update_layout(title='Frequency Spectrum Analysis Data', xaxis_title='Frequency (Hz)', yaxis_title='Magnitude')

fig_fft.show()

# A Sample of a Cascade Plot
## Time Waveforms or Spectra are Taken over a Period of Time, Then Plotted in a 3D space
### The Y-Axis of a Cascade Plot is the Date/Time of the Data Snapshot.
#### This Technique is Useful for Identifying the Condition of a Machine Deteriorating, EX: A Bearing Frequency Amplitude Increases Over a Period of Several Weeks.

In [11]:
# Set up the time array for each waveform
t = np.linspace(0, 2, 500) # 2 seconds period, 500 points

# Create a time series for the dates
dates = pd.date_range(start='1/1/2023', end='10/31/2023', periods=20)

# Initialize lists to store the data
data_blue = []
data_red = []
data_green = []

amp_blue, amp_red, amp_green = 1,2,3
f=25

# Generate the data
for i, date in enumerate(dates):
    # Create a damping factor (decreasing over time)
    damping = (20 - i) / 20

    # Create the waveforms
    blue = damping * amp_blue * np.sin(2 * np.pi * f * t)
    red = damping * amp_red * np.sin((2 * np.pi * f * t) + shift_phase(90))
    green = damping * amp_green * np.sin((2 * np.pi * f * t) + shift_phase(45))

    # Append the data
    data_blue.append(blue)
    data_red.append(red)
    data_green.append(green)

# Create the waterfall plot
fig_waterfall = go.Figure()

# Add the traces
for i, date in enumerate(dates):
    fig_waterfall.add_trace(go.Scatter3d(x=t, y=[date]*len(t), z=data_blue[i], mode='lines', name=f'Axis 1 - {date}', line=dict(color='blue')))
    fig_waterfall.add_trace(go.Scatter3d(x=t, y=[date]*len(t), z=data_red[i], mode='lines', name=f'Axis 2 - {date}', line=dict(color='red')))
    fig_waterfall.add_trace(go.Scatter3d(x=t, y=[date]*len(t), z=data_green[i], mode='lines', name=f'Axis 3 - {date}', line=dict(color='green')))

# Update the layout
fig_waterfall.update_layout(scene=dict(xaxis_title='Time (s)', yaxis_title='Date', zaxis_title='Acceleration (g)', aspectratio=dict(x=2, y=1, z=1)))
fig_waterfall.update_layout(title='Waterfall Plot of Time Waveform Analysis Data')

fig_waterfall.show()